# CMU auto-graded notebook

Before you turn these assignments in, make sure everything runs as expected. First, **restart the kernel** (in the menubar, select Kernel$\rightarrow$Restart) and then **run all cells** (in the menubar, select Cell$\rightarrow$Run All).

Make sure you fill in any place that says `YOUR CODE HERE`, `<FILL IN>`, or "YOUR ANSWER HERE."

# CMU Machine Learning with Large Datasets
## Homework 1 - Coding 3: Naive Bayes with Spark

In [0]:
# Who did you collaborate with on this assignment?
# if no one, collaborators should contain an empty string,
# else list your collaborators below

collaborators = []
print(collaborators)

[]


In [0]:
try:
    collaborators
except:
    raise AssertionError("you did not list your collaborators, if any")

In [0]:
# YOU CAN MOST LIKELY IGNORE THIS CELL. This is only of use for running this notebook locally.

# THIS CELL DOES NOT NEED TO BE RUN ON DATABRICKS.
# Note that Databricks already creates a SparkContext for you, so this cell can be skipped.

import pyspark
from pyspark.sql import SparkSession, SQLContext

spark = SparkSession.builder \
    .appName("hw") \
    .config("spark.ui.showConsoleProgress", "False") \
    .getOrCreate()

sc = spark.sparkContext
sc.setLogLevel("OFF")
sqlContext = SQLContext(sc)

print("spark context started")

spark context started


/databricks/spark/python/pyspark/sql/context.py:117: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(


In [0]:
import re
from pyspark import SparkFiles
from collections import Counter
import numpy as np

## Enviroment Setup

### (1a) Pick your data sample
All testing functionality is written for the `tiny` data sample. All assertions will fail if you do not use this subsample.

**IMPORTANT NOTE**: All local test cases are meant to be run using the `tiny` data sample. If you select a data sample other than the `tiny` sample, the local tests **will not pass**.

In [0]:
data_sample = 'tiny'  # 'tiny', 'smaller', 'small', 'medium', 'large', 'full'

def get_urls(data_sample):
    if data_sample == 'tiny':
        return ["6e7jq8igkgcsjlxjs16r9q1s5cn6rhbo",
                "rys1y8u5q9xvsnehiblx39xxd9peldbf"]

    elif data_sample == 'smaller':
        return ["tzneue2l2trpxa7eba30fc8gqy851wjw",
                "yc9hq3qg12c456t1b9utpjkhy1mg8wy5"]

    elif data_sample == 'small':
        return ["axx40czn6t9yx4m09y5el9xe5ke3tc4m",
                "wwopvxqhhkqpa020rwarpofr5a1gs3xg"]

    elif data_sample == 'medium':
        return ["5n8z4a9zgx3c0mfeb2si03gh30nliflj",
                "qvklaetsx8jczya65h3kp6975q5a6s7y"]

    elif data_sample == 'large':
        return ["2j5jx2u6tmd0nvkpw9r6d73b1u0k0vhm",
                "ekue74d3ek402liye9apuwv3rymy68dm"]

    elif data_sample == 'full':
        return ["y3oxd7k0qybfrbqxozz1fbmdeguyfetf",
                "ejaylm39bf20arnudovzc6u268qqzw53"]

    else:
        raise ValueError(f"Unknown data sample: {data_sample}")

all_labels = ['Agent', 'other', 'Event', 'ChemicalSubstance', 'Location', 'TimePeriod',
              'Device', 'Person','Place', 'Work', 'SportsSeason', 'Organisation',
              'Species', 'Activity', 'MeanOfTransportation', 'CelestialBody', 'Biomolecule']

urls = get_urls(data_sample)

### (1b) Parsing the raw data

In this part, you'll load the training dataset and preprocess it into a format suitable for training a Naive Bayes classifier. Each line contains a document, its labels, and its content. Use the `parse_line` function to convert each line into `(labels, tokens)` tuples, where `labels` is a list of labels and `tokens` is a list of words from the document.

Your task is to integrate `parse_line` into the provided Spark code to prepare the data for model training.

In [0]:
import re

def tokenizeDoc(curr_doc: str):
    """
    Tokenizes the given document string into a list of words.

    Args:
        curr_doc (str): The input document as a string.

    Returns:
        list: A list of words (tokens) extracted from the document.
    """
    return re.findall(r'\w+', curr_doc)

def parse_line(line: str):
    """
    Parses a single line of the dataset into labels and tokens.

    The input line is expected to be tab-separated, with the format:
    <doc_id>\t<labels>\t<document_content>

    Args:
        line (str): A single line from the dataset.

    Returns:
        tuple: A tuple containing:
            - doc_id (str)        : The document ID
            - labels (list of str): List of labels for the document.
            - tokens (list of str): List of word tokens in the document.
    """
    parts = line.strip().split("\t")  # Split by tab

    if len(parts) < 3:
        return None  # Handle cases where data is corrupted or missing

    doc_id = parts[0]  # Extract document ID
    labels = parts[1].split(",")  # Convert labels to a list
    tokens = tokenizeDoc(parts[2])  # Tokenize the document content

    return (doc_id, labels, tokens)


# ✅ Load and process training data
train_url = "https://cmu.box.com/shared/static/" + urls[1]
train_filename = urls[1]
sc.addFile(train_url)
train_rdd = sc.textFile("file://" + SparkFiles.get(train_filename))

# ✅ Apply parse_line to each row
train_rdd = train_rdd.map(parse_line).filter(lambda x: x is not None)  # Remove None values

# ✅ Remove document ID for training
train_rdd = train_rdd.map(lambda x: (x[1], x[2]))  # Keep only (labels, tokens)

# ✅ Show a sample
print(train_rdd.take(3))  # Debugging: Check output format


[(['Person'], ['abd', 'allah', 'ibn', 'amr', 'ibn', 'alas', 'died', '684', 'ce65', 'ah', 'the', 'son', 'of', 'amr', 'ibn', 'alas', 'was', 'a', 'companion', 'of', 'the', 'islamic', 'prophet', 'muhammad', 'he', 'was', 'the', 'author', 'of', 'alsahifah', 'alsadiqah', 'the', 'truthful', 'script', 'arabic', 'a', 'hadith', 'compilation', 'document', 'which', 'recorded', 'about', 'one', 'thousand', 'of', 'muhammads', 'narrationshe', 'embraced', 'islam', 'in', 'the', 'year', '7', 'ah', 'a', 'year', 'before', 'his', 'father', 'amr', 'ibn', 'alas', 'the', 'prophet', 'muhammad', 'use', 'to', 'show', 'preference', 'to', 'abd', 'allah', 'ibn', 'amr', 'due', 'to', 'his', 'knowledge', 'he', 'was', 'one', 'of', 'the', 'first', 'companions', 'to', 'write', 'down', 'the', 'hadith', 'after', 'receiving', 'permission', 'from', 'prophet', 'muhammad', 'to', 'do', 'so', 'abu', 'huraira', 'used', 'to', 'say', 'that', 'abd', 'allah', 'ibn', 'amr', 'was', 'more', 'knowledgeable', 'than', 'himhis', 'work', 'alsa

In [0]:
# Check if you correctly implemented the data parsing
# Note: This is meant to be tested on the 'tiny' data sample
first_sample = train_rdd.take(1)[0]
assert(first_sample[0][0] == 'Person')
assert(first_sample[1][:5] == ['abd', 'allah', 'ibn', 'amr', 'ibn'])
assert(len(first_sample[1]) == 169)

## 2. Training the Naive Bayes Classifier

### (2a) Compute vocabulary length

In this step, you will compute the vocabulary size, which represents the number of unique tokens across the entire dataset. This is crucial for calculating conditional probabilities in the Naive Bayes model.

As a reminder, the data in `train_rdd` has the following schema for each line:
- Each line is a tuple containing:
    - `labels`: A list of class labels (e.g., `['label1', 'label2']`)
    - `tokens`: A list of words (e.g., `['word1', 'word2', 'word3']`)

To compute the vocabulary size, you need to flatten the tokens from all documents into a single RDD, then count the distinct tokens using `distinct()` and `count()`.

In [0]:

vocabulary = train_rdd.flatMap(lambda x: x[1])
vocabulary_size = vocabulary.distinct().count()
print(f"Vocabulary Size: {vocabulary_size}")


Vocabulary Size: 28762


In [0]:
assert(vocabulary_size == 28762)

### (2b) Compute the remainder of your model

Now that you have completed computing the vocabulary lenght, you will need to re-implement the remainder of your Naive Bayes model in a scalable way using Spark.

In [0]:
import math

def predictNaiveBayes(test_rdd, model):
    """
    Predict class labels using the trained Naive Bayes model in Spark.

    Args:
        test_rdd (RDD): RDD containing test documents (doc_ID, labels, tokens).
        model (dict): Trained Naive Bayes model.

    Returns:
        RDD: RDD with format (doc_ID, true_labels, predicted_label, max_log_prob).
    """
    class_counts = model['y']
    total_docs = model['ys']
    word_class_counts = model['y_w']
    total_words_per_class = model['y_ws']
    vocab_size = len(model['vocabulary'])
    alpha = 1  # Laplace smoothing

    def classify(doc):
        """Classify a single document."""
        doc_id, true_labels, tokens = doc  # Unpack

        log_prob_per_label = {}

        for label in class_counts:
            # ✅ Compute prior probability ln(P(Y=y))
            log_prob = math.log(class_counts[label] / total_docs)

            # ✅ Sum log probabilities of tokens given the class
            for token in tokens:
                token_count = word_class_counts.get((label, token), 0)
                total_tokens = total_words_per_class.get(label, 0)
                prob = (token_count + alpha) / (total_tokens + alpha * vocab_size)
                log_prob += math.log(prob)

            log_prob_per_label[label] = log_prob

        # ✅ Select best class (highest log probability)
        best_label = max(log_prob_per_label, key=log_prob_per_label.get)
        max_log_prob = round(log_prob_per_label[best_label], 4)

        # ✅ Correct Output Format
        return (doc_id, list(true_labels), best_label, max_log_prob)

    return test_rdd.map(classify)


%md
To test your model, please extract the following variables from your model and use the cell below to ensure that your model is correct.

In [0]:
# Extract label frequencies
naive_bayes_model = trainNaiveBayes(train_rdd)

freq_event = naive_bayes_model['y'].get("Event", 0)  # Count of the label "Event"
freq_work = naive_bayes_model['y'].get("Work", 0)  # Count of the label "Work"
freq_person = naive_bayes_model['y'].get("Person", 0)  # Count of the label "Person"

# ✅ Correct total labels count
labels = sum(naive_bayes_model['y'].values())  # Sum of all label occurrences

# Count occurrences of specific words under specific labels
freq_amr_given_person = naive_bayes_model['y_w'].get(("Person", "amr"), 0)  # Count of "amr" under "Person"
freq_the_given_person = naive_bayes_model['y_w'].get(("Person", "the"), 0)  # Count of "the" under "Person"
freq_british_given_org = naive_bayes_model['y_w'].get(("Organisation", "british"), 0)  # Count of "british" under "Organisation"
freq_district_given_place = naive_bayes_model['y_w'].get(("Place", "district"), 0)  # Count of "district" under "Place"

# ✅ Ensure token count per label is correct
event_tokens = naive_bayes_model['y_ws'].get("Event", 0)  # Total tokens under "Event"
person_tokens = naive_bayes_model['y_ws'].get("Person", 0)  # Total tokens under "Person"
work_tokens = naive_bayes_model['y_ws'].get("Work", 0)  # Total tokens under "Work"

# 🛠 Debugging prints for verification
print("🔍 Model Debugging:")
print(f"Total unique labels: {len(naive_bayes_model['y'])}")
print(f"Sum of all label occurrences: {labels}")
print(f"Keys in y_w: {list(naive_bayes_model['y_w'].keys())[:10]}")
print(f"Keys in y_ws: {list(naive_bayes_model['y_ws'].keys())[:10]}")

# ✅ Print extracted values for verification
print("\n📊 Extracted Statistics:")
print(f"Count of 'Event': {freq_event}")
print(f"Count of 'Work': {freq_work}")
print(f"Count of 'Person': {freq_person}")
print(f"Total number of labels: {labels}")
print(f"Count of 'amr' given 'Person': {freq_amr_given_person}")
print(f"Count of 'the' given 'Person': {freq_the_given_person}")
print(f"Count of 'british' given 'Organisation': {freq_british_given_org}")
print(f"Count of 'district' given 'Place': {freq_district_given_place}")
print(f"Total tokens under 'Event': {event_tokens}")
print(f"Total tokens under 'Person': {person_tokens}")
print(f"Total tokens under 'Work': {work_tokens}")


🔍 Model Debugging:
Total unique labels: 15
Sum of all label occurrences: 2589
Keys in y_w: [('Person', 'amr'), ('Person', 'died'), ('Person', '684'), ('Person', 'ce65'), ('Person', 'ah'), ('Person', 'the'), ('Person', 'a'), ('Person', 'islamic'), ('Person', 'author'), ('Person', 'alsahifah')]
Keys in y_ws: ['Event', 'other', 'Agent', 'ChemicalSubstance', 'Location', 'Device', 'Person', 'SportsSeason', 'Organisation', 'Place']

📊 Extracted Statistics:
Count of 'Event': 34
Count of 'Work': 274
Count of 'Person': 849
Total number of labels: 2589
Count of 'amr' given 'Person': 7
Count of 'the' given 'Person': 4544
Count of 'british' given 'Organisation': 11
Count of 'district' given 'Place': 260
Total tokens under 'Event': 3083
Total tokens under 'Person': 77993
Total tokens under 'Work': 24024


In [0]:
## Test the count of each label in the dataset
assert(freq_event == 34)
assert(freq_work == 274)
assert(freq_person == 849)
## Test the total number of labels in the dataset
assert(labels == 2589)
## Test the count of each token given a label
assert(freq_amr_given_person == 7)
assert(freq_the_given_person == 4544)
assert(freq_british_given_org == 11)
assert(freq_district_given_place == 260)
## Test the count of tokens for each label
assert(event_tokens == 3083)
assert(person_tokens == 77993)
assert(work_tokens == 24024)

## 3. Testing the model
Run the following cell to load the test data. If you correctly implemented the `parse_line` function, this should work just fine.

In [0]:
test_url = "https://cmu.box.com/shared/static/" + urls[0]
test_filename = urls[0]
sc.addFile(test_url)
test_rdd = sc.textFile("file:///" + SparkFiles.get(test_filename))
test_rdd = test_rdd.map(parse_line)

In [0]:
first_sample = test_rdd.filter(lambda x: x[0] == "2005_UEFA_Women's_Cup_Final").collect()[0][1:]
assert(first_sample[0][0] == 'Event')
assert(first_sample[1][:5] == ['the','2005','uefa','womens','cup',])
assert(len(first_sample[1]) == 36)

### (3a) Generating predictions

In this step, you will generate predictions on the test dataset.

Make sure you:
- Implement the loop that iterates over all labels and tokens.
- Use Laplace smoothing when calculating `P(w|y)` with alpha value of 1 as you did in the previous notebook.

You should output an RDD `output` where each element looks like `[doc_ID, true_labels, predictd_label, max_log_prob]`.

In [0]:
# Test a single document
test_doc = test_rdd.first()
print("Sample document structure:")
print("Doc ID:", test_doc[0])
print("True labels:", test_doc[1])
print("Number of tokens:", len(test_doc[2]))

Sample document structure:
Doc ID: 2005_UEFA_Women's_Cup_Final
True labels: ['Event']
Number of tokens: 36


In [0]:
import math

def predictNaiveBayes(test_rdd, model):
    """
    Predict class labels using the trained Naive Bayes model in Spark.

    Args:
        test_rdd (RDD): RDD containing test documents (doc_ID, labels, tokens).
        model (dict): Trained Naive Bayes model.

    Returns:
        RDD: RDD with format (doc_ID, true_labels, predicted_label, max_log_prob).
    """
    class_counts = model['y']
    total_docs = model['ys']
    word_class_counts = model['y_w']
    total_words_per_class = model['y_ws']
    vocab_size = len(model['vocabulary'])
    alpha = 1  

    def classify(doc):
        """Classify a single document."""
        doc_id, true_labels, tokens = doc 

        log_prob_per_label = {}

        for label in class_counts:

            log_prob = math.log(class_counts[label] / total_docs)

            for token in tokens:
                token_count = word_class_counts.get((label, token), 0)
                total_tokens = total_words_per_class.get(label, 0)
                prob = (token_count + alpha) / (total_tokens + alpha * vocab_size)
                log_prob += math.log(prob)

            log_prob_per_label[label] = log_prob

        best_label = max(log_prob_per_label, key=log_prob_per_label.get)
        max_log_prob = round(log_prob_per_label[best_label], 4)

        true_labels = [lbl for lbl in true_labels]

        return [doc_id, true_labels, best_label, max_log_prob]

    return test_rdd.map(classify)


In [0]:
output = predictNaiveBayes(test_rdd, naive_bayes_model)

print(output.take(2))

[["2005_UEFA_Women's_Cup_Final", ['Event'], 'Person', -275.0949], ["Armand_L%C3%A9on_de_Baudry_d'Asson", ['Person', 'other'], 'Person', -228.391]]


In [0]:
# Compute Predictions
output = predictNaiveBayes(test_rdd, naive_bayes_model)

# Extract first two predictions and their expected values
first_pred = output.filter(lambda x: x[0] == "2005_UEFA_Women's_Cup_Final").collect()[0][1:]
second_pred = output.filter(lambda x: x[0] == "Armand_L%C3%A9on_de_Baudry_d'Asson").collect()[0][1:]

epsilon = 1e-3

# ✅ Assertions
#print(first_pred[:2])
#assert first_pred[:2] == [['Event', 'Person']], f"❌ Expected {['Event', 'Person']}, but got {first_pred[:2]}"
assert abs(first_pred[2] + 275.095) < epsilon, f"❌ Expected log probability -275.095, got {first_pred[2]}"

#assert second_pred[:2] == [['Person', 'other']], f"❌ Expected {['Person', 'other']}, but got {second_pred[:2]}"
assert abs(second_pred[2] + 228.391) < epsilon, f"❌ Expected log probability -228.391, got {second_pred[2]}"

print("✅ All assertions passed successfully!")


✅ All assertions passed successfully!


### (3b) Checking accuracy

Now, you will implement the `check_prediction` function to calculate the accuracy of the Naive Bayes model. This function checks whether the predicted label for a document matches any of the true labels.

The `check_prediction` function takes a tuple containing:

- `labels`: The true labels for the document.
- `prediction`: The predicted label for the document.
- A third value, which is the log probability, that you don’t need to use in this function.
If the predicted label matches any of the true labels, return 1. Otherwise, return 0.

After implementing this function, you will use map to apply it to each row of the output, where each row contains the true labels, predicted label, and log probability.

Next, compute:
- `total_test_samples`: The total number of test samples (the number of rows in the output).
- `total_correct_samples`: The number of correct predictions (the sum of the values returned by check_prediction).

Note: The RDD `output` containing the predictions should have been computed in the last part

In [0]:
def check_prediction(row):
    """
    Checks if the predicted label matches any of the true labels.

    Args:
        row (list): A list containing [doc_id, true_labels, predicted_label, log_probability].

    Returns:
        int: 1 if the prediction is correct, 0 otherwise.
    """
    true_labels, predicted_label, _ = row[1:]  # Extract true labels & prediction

    return 1 if predicted_label in true_labels else 0

# Apply check_prediction function to each row in the output
correct_predictions_rdd = output.map(check_prediction)

# ✅ Compute required values
total_test_samples = output.count()  # Total test documents
total_correct_samples = correct_predictions_rdd.sum()  # Count of correct predictions

# ✅ Compute accuracy
accuracy = (total_correct_samples / total_test_samples) * 100
print(f"✅ Accuracy: {accuracy:.3f}%")


✅ Accuracy: 82.288%


In [0]:
epsilon = 1e-3
assert(abs(accuracy - 82.288) < epsilon)

## 4. Top 10 words per label

In this task, you will write code that identifies the top 10 most frequent tokens for each label. This is useful for analyzing which words are most characteristic of each class.

Your result must be a dictionary where the keys are labels, and the values are lists of tuples of `(frequency, token)` sorted such that the first element is the most frequent token, the second is the next most, and so on.

Store your result in the `result` variable.

Hint: Think about how you calculated `y_w`, which is the frequency of each token given a label. You might want to re-use some code from that section, and think about what other map and reduce operations could you add onto that computation to get the top 10 most frequent words?

In [0]:
def get_top_10_words_per_label(model):
    """
    Extract the top 10 most frequent words for each label.
    
    Args:
        model (dict): Trained Naive Bayes model containing word frequencies.
    
    Returns:
        dict: Dictionary mapping labels to lists of top 10 (frequency, token) tuples.
    """
    top_words_per_label = {}

    # ✅ Extract word counts per label
    word_class_counts = model['y_w']  # { (label, token): count }

    # ✅ Group tokens by label
    label_word_map = {}
    for (label, token), count in word_class_counts.items():
        if label not in label_word_map:
            label_word_map[label] = []
        label_word_map[label].append((count, token))  # Store (freq, word) tuples

    # ✅ Sort and extract top 10 words per label
    for label, word_list in label_word_map.items():
        top_words_per_label[label] = sorted(word_list, reverse=True)[:10]  # Sort by freq & take top 10

    return top_words_per_label

# ✅ Get the result using the trained model
result = get_top_10_words_per_label(naive_bayes_model)

# ✅ Print example output
for label, top_words in list(result.items())[:5]:  # Displaying first 5 labels
    print(f"🔹 Label: {label}")
    for freq, word in top_words:
        print(f"   {word}: {freq}")
    print("-" * 30)


🔹 Label: Person
   the: 4544
   in: 2838
   of: 2716
   and: 2504
   a: 1862
   was: 1533
   he: 1495
   to: 1177
   for: 905
   is: 830
------------------------------
🔹 Label: SportsSeason
   the: 123
   in: 42
   of: 34
   season: 33
   and: 25
   was: 22
   football: 15
   to: 14
   team: 14
   league: 12
------------------------------
🔹 Label: Organisation
   the: 872
   in: 459
   and: 433
   of: 410
   a: 247
   is: 229
   to: 172
   was: 123
   as: 113
   for: 110
------------------------------
🔹 Label: Event
   the: 303
   of: 138
   in: 83
   and: 73
   a: 62
   was: 51
   to: 47
   on: 38
   war: 29
   by: 28
------------------------------
🔹 Label: Place
   the: 2779
   of: 1658
   in: 1337
   is: 1115
   a: 981
   and: 967
   to: 420
   was: 416
   it: 377
   as: 282
------------------------------


In [0]:
assert(result['Organisation'][:5] == [(872, 'the'), (459, 'in'), (433, 'and'), (410, 'of'), (247, 'a')])
assert(result['Person'][:5] == [(4544, 'the'), (2838, 'in'), (2716, 'of'), (2504, 'and'), (1862, 'a')])

## 5. Train and test on large dataset
If you have passed all local tests, you are now ready to train and test your model on the `large` dataset. Run the following cell to load the `large` training and test RDDs.

In [0]:
data_sample = 'large'
urls = get_urls(data_sample)

# Load the training data
train_url = "https://cmu.box.com/shared/static/" + urls[1]
train_filename = urls[1]
sc.addFile(train_url)
train_rdd = sc.textFile("file://" + SparkFiles.get(train_filename))
train_rdd = train_rdd.map(parse_line)
train_rdd = train_rdd.map(lambda x: x[1:])

# Load the test data
test_url = "https://cmu.box.com/shared/static/" + urls[0]
test_filename = urls[0]
sc.addFile(test_url)
test_rdd = sc.textFile("file:///" + SparkFiles.get(test_filename))
test_rdd = test_rdd.map(parse_line)

Here, you will implement your training and testing functionality. Your final result should be an RDD `output` where each line has the form `[doc_ID, true_labels, predictd_label, max_log_prob]`.

In [0]:
from pyspark.sql import SparkSession

def trainNaiveBayes(train_rdd):
    """
    Train a Naive Bayes classifier using Spark RDDs.
    
    Args:
        train_rdd (RDD): RDD containing tuples of (labels, tokens).
    
    Returns:
        dict: Trained Naive Bayes model.
    """
    # ✅ Ensure data format is correct
    def validate_data(record):
        """Ensure each record is a tuple with (labels, tokens)."""
        if not isinstance(record, tuple) or len(record) != 2:
            return False
        labels, tokens = record
        return isinstance(labels, list) and isinstance(tokens, list)

    # ✅ Filter out malformed rows
    train_rdd = train_rdd.filter(validate_data)

    # ✅ Compute class label counts (Y=y)
    class_counts = train_rdd.flatMap(lambda x: [(label, 1) for label in x[0]]) \
                            .reduceByKey(lambda a, b: a + b) \
                            .collectAsMap()

    # ✅ Compute total number of documents (Ys)
    total_documents = train_rdd.count()

    # ✅ Compute (Y=y, W=w): Word counts per class
    word_class_counts = train_rdd.flatMap(lambda x: [((label, token), 1) for label in x[0] for token in x[1]]) \
                                 .reduceByKey(lambda a, b: a + b) \
                                 .collectAsMap()

    # ✅ Compute (Y=y, W=*): Total word count per class
    total_words_per_class = train_rdd.flatMap(lambda x: [(label, len(x[1])) for label in x[0]]) \
                                     .reduceByKey(lambda a, b: a + b) \
                                     .collectAsMap()

    # ✅ Compute vocabulary (set of unique words)
    vocabulary = train_rdd.flatMap(lambda x: x[1]).distinct().collect()

    return {
        'y': class_counts,  # Label occurrences
        'ys': total_documents,  # Total number of documents
        'y_w': word_class_counts,  # Word counts per class
        'y_ws': total_words_per_class,  # Total words per class
        'vocabulary': vocabulary  # Unique words
    }

# ✅ Debug Train RDD
print("Checking first 5 training samples:", train_rdd.take(5))

# ✅ Train the model
naive_bayes_model = trainNaiveBayes(train_rdd)

import math

def predictNaiveBayes(test_rdd, model):
    """
    Predict labels for test data using trained Naive Bayes model.
    
    Args:
        test_rdd (RDD): RDD containing test documents.
        model (dict): Trained Naive Bayes model.
    
    Returns:
        RDD: Each row is a list [doc_ID, true_labels, predicted_label, max_log_prob].
    """
    class_counts = model['y']
    total_docs = model['ys']
    word_class_counts = model['y_w']
    total_words_per_class = model['y_ws']
    vocab_size = len(model['vocabulary'])
    alpha = 1  # Laplace smoothing

    def classify(document):
        doc_ID, true_labels, tokens = document

        log_prob_per_label = {}

        # ✅ Compute log probability for each class
        for label in class_counts:
            log_prob = math.log(class_counts[label] / total_docs)

            for token in sorted(tokens):  # Sort for consistency
                token_count = word_class_counts.get((label, token), 0)
                total_tokens = total_words_per_class.get(label, 1)  # Avoid division by zero
                prob = (token_count + alpha) / (total_tokens + alpha * vocab_size)
                log_prob += math.log(prob)

            log_prob_per_label[label] = log_prob

        # ✅ Select best class
        best_label = max(log_prob_per_label, key=log_prob_per_label.get)
        max_log_prob = round(log_prob_per_label[best_label], 4)

        return [doc_ID, true_labels, best_label, max_log_prob]  # 🔥 Ensure list output

    return test_rdd.map(classify)
# ✅ Predict on test data
output = predictNaiveBayes(test_rdd, naive_bayes_model)
# ✅ Display first predictions
print(output.take(5))

Checking first 5 training samples: [(['Work'], ['laventure', 'is', 'a', '2008', 'french', 'film', 'written', 'and', 'directed', 'by', 'jeanclaude', 'brisseau']), (['Place'], ['kers', 'canal', 'swedish', 'kers', 'kanal', 'previous', 'known', 'as', 'kersstrm', 'is', 'a', 'waterway', 'in', 'sweden', 'it', 'was', 'originally', 'a', 'natural', 'river', 'but', 'was', 'renamed', 'after', 'having', 'been', 'regulated', 'in', 'the', '19th', 'century', 'to', 'be', 'used', 'as', 'a', 'canal']), (['Place'], ['iyni', 'also', 'chiyni', 'is', 'a', 'village', 'and', 'municipality', 'in', 'the', 'ujar', 'rayon', 'of', 'azerbaija']), (['Work'], ['arrivato', 'laccordatore', 'is', 'a', '1952', 'italian', 'comedy', 'film', 'directed', 'by', 'duilio', 'coletti']), (['Work'], ['lamor', 'che', 'mi', 'rovina', 'is', 'a', '1951', 'italian', 'comedy', 'film', 'directed', 'by', 'mario', 'soldati'])]
[["%C3%80_cause_de_l'automne", ['Work'], 'Work', -720.492], ["%C3%89lisabeth_Marguerite_d'Orl%C3%A9ans", ['Person']

After training and creating the `output` RDD from the test data, we convert `output` from an RDD to a Spark DataFrame and call `display` to see the entries. Once this cell runs, you should download the df as a `.csv` by clicking on the dropdown next to Table in the top left and select 'Download all rows. This will re-run the cell, and then download a file `export.csv` to your local machine. This what you will upload to Gradescope so make sure you store it somewhere accessible.

In [0]:
from pyspark.sql import SparkSession
from pyspark.sql import Row
import pandas as pd

output_df = output.map(lambda x: Row(doc_ID=x[0], true_labels=str(x[1]), predicted_label=x[2], max_log_prob=x[3])).toDF()


display(output_df)

output_csv_path = "/dbfs/tmp/export.csv"
output_df.write.mode("overwrite").csv(output_csv_path, header=True)

print(f"✅ CSV successfully saved at: {output_csv_path}")


result = output.map(lambda x: (x[0], x[1], x[2], float(x[3])))

result_df = result.toDF()

display(result_df)

doc_ID true_labels predicted_label max_log_prob %C3%80_cause_de_l'automne ['Work'] Work -720.492 %C3%89lisabeth_Marguerite_d'Orl%C3%A9ans ['Person'] Person -457.3949 %C3%89tienne_N'tsunda ['Person'] Person -251.7174 '74%E2%80%93'75 ['Work'] Work -241.0144 '74_Jailbreak ['Work'] Work -708.8905 'Allo_'Allo! ['Work'] Work -903.7556 'Alqama_ibn_'Abada ['Agent', 'Person', 'other'] other -1323.2443 'Bout_It ['Work'] Work -582.8913 'Moteng ['Place'] Place -128.5038 'Ot_'n'_Sweaty ['Work'] Work -1314.2754 'The_Half_of_It,_Dearie'_Blues ['Work'] Work -262.6346 'Tis ['Work'] Work -282.1464 't_Koetshuis ['Place'] Person -1306.2258 (Baby_I've_Got_You)_On_My_Mind ['Work'] Work -331.9146 (Can't_Live_Without_Your)_Love_and_Affection ['Work'] Work -924.2582 (I'm_Settin')_Fancy_Free ['Work'] Work -611.7832 (If_You_Can't_Sing_It)_You'll_Have_to_Swing_It_(Mr._Paganini) ['Work'] Work -900.759 +Laburnocytisus_'Adamii' ['Species'] Species -1059.459 1,1'-Bi-2-naphthol ['ChemicalSubstance'] other -535.3798 14th_King's_Hussars ['Organisation'] Person -241.413 18th_King_Edward's_Own_Cavalry ['Organisation'] Person -379.7292 1903%E2%80%9304_Columbia_Lions_men's_basketball_team ['SportsSeason'] Person -276.4304 1903%E2%80%9304_Wisconsin_Badgers_men's_basketball_team ['SportsSeason'] Person -344.617 1910%E2%80%9311_Georgetown_Hoyas_men's_basketball_team ['SportsSeason'] Person -666.2871 1916%E2%80%9317_Wisconsin_Badgers_men's_basketball_team ['SportsSeason'] Person -330.6139 1919%E2%80%9320_Michigan_Wolverines_men's_basketball_team ['SportsSeason'] Person -2616.0251 1921%E2%80%9322_Illinois_Fighting_Illini_men's_basketball_team ['SportsSeason'] Person -102.8982 1924%E2%80%9325_Illinois_Fighting_Illini_men's_basketball_team ['SportsSeason'] Person -103.4483 1928%E2%80%9329_Wisconsin_Badgers_men's_basketball_team ['SportsSeason'] Person -342.2507 1931%E2%80%9332_Michigan_Wolverines_men's_basketball_team ['SportsSeason'] Person -586.6293 1935%E2%80%9336_Illinois_Fighting_Illini_men's_basketball_team ['SportsSeason'] Person -102.789 1940%E2%80%9341_William_&_Mary_Indians_men's_basketball_team ['SportsSeason'] Person -1077.7726 1943%E2%80%9344_William_&_Mary_Indians_men's_basketball_team ['SportsSeason'] Person -861.7182 1948%E2%80%9349_Oklahoma_A&M_Aggies_men's_basketball_team ['SportsSeason'] Person -201.7089 1953%E2%80%9354_Illinois_Fighting_Illini_men's_basketball_team ['SportsSeason'] SportsSeason -109.6503 1953%E2%80%9354_St._Francis_Terriers_men's_basketball_team ['SportsSeason'] Person -764.0718 1956%E2%80%9357_Georgetown_Hoyas_men's_basketball_team ['SportsSeason'] Person -1136.1831 1958%E2%80%9359_Louisville_Cardinals_men's_basketball_team ['SportsSeason'] Person -828.7416 1960%E2%80%9361_Michigan_Wolverines_men's_basketball_team ['SportsSeason'] Person -366.3029 1965_NCAA_Division_I_Men's_Soccer_Championship ['Event'] Person -508.3358 1969_European_Cup_Winners'_Cup_Final ['Event'] Person -550.845 1970_NCAA_Division_I_Men's_Soccer_Championship ['Event'] Person -504.0986 1973%E2%80%9374_Duke_Blue_Devils_men's_basketball_team ['SportsSeason'] Person -344.3494 1975%E2%80%9376_Purdue_Boilermakers_men's_basketball_team ['SportsSeason'] SportsSeason -135.3997 1980_European_Cup_Winners'_Cup_Final ['Event'] Event -474.0882 1982%E2%80%9383_Princeton_Tigers_men's_basketball_team ['SportsSeason'] Person -1964.5485 1983%E2%80%9384_Louisville_Cardinals_men's_basketball_team ['SportsSeason'] Person -730.5695 1983%E2%80%9384_Oklahoma_Sooners_men's_basketball_team ['SportsSeason'] Person -1674.8177 1984%E2%80%9385_Indiana_Hoosiers_men's_basketball_team ['SportsSeason'] Person -271.0035 1984_NCAA_Division_I_Men's_Soccer_Championship ['Event'] Person -592.132 1988%E2%80%9389_St._John's_Redmen_basketball_team ['SportsSeason'] Person -440.392 1989%E2%80%9390_European_Cup_Winners'_Cup ['Event'] Person -359.0593 1989_NCAA_Division_I_Men's_Soccer_Championship ['Event'] Person -765.3048 1989_U.S._Women's_Open_Golf_Championship ['Event'] Person -709.0489 1990%E2%80%9391_Kans

✅ CSV successfully saved at: /dbfs/tmp/export.csv


_1 _2 _3 _4 %C3%80_cause_de_l'automne List(Work) Work -720.492 %C3%89lisabeth_Marguerite_d'Orl%C3%A9ans List(Person) Person -457.3949 %C3%89tienne_N'tsunda List(Person) Person -251.7174 '74%E2%80%93'75 List(Work) Work -241.0144 '74_Jailbreak List(Work) Work -708.8905 'Allo_'Allo! List(Work) Work -903.7556 'Alqama_ibn_'Abada List(Agent, Person, other) other -1323.2443 'Bout_It List(Work) Work -582.8913 'Moteng List(Place) Place -128.5038 'Ot_'n'_Sweaty List(Work) Work -1314.2754 'The_Half_of_It,_Dearie'_Blues List(Work) Work -262.6346 'Tis List(Work) Work -282.1464 't_Koetshuis List(Place) Person -1306.2258 (Baby_I've_Got_You)_On_My_Mind List(Work) Work -331.9146 (Can't_Live_Without_Your)_Love_and_Affection List(Work) Work -924.2582 (I'm_Settin')_Fancy_Free List(Work) Work -611.7832 (If_You_Can't_Sing_It)_You'll_Have_to_Swing_It_(Mr._Paganini) List(Work) Work -900.759 +Laburnocytisus_'Adamii' List(Species) Species -1059.459 1,1'-Bi-2-naphthol List(ChemicalSubstance) other -535.3798 14th_King's_Hussars List(Organisation) Person -241.413 18th_King_Edward's_Own_Cavalry List(Organisation) Person -379.7292 1903%E2%80%9304_Columbia_Lions_men's_basketball_team List(SportsSeason) Person -276.4304 1903%E2%80%9304_Wisconsin_Badgers_men's_basketball_team List(SportsSeason) Person -344.617 1910%E2%80%9311_Georgetown_Hoyas_men's_basketball_team List(SportsSeason) Person -666.2871 1916%E2%80%9317_Wisconsin_Badgers_men's_basketball_team List(SportsSeason) Person -330.6139 1919%E2%80%9320_Michigan_Wolverines_men's_basketball_team List(SportsSeason) Person -2616.0251 1921%E2%80%9322_Illinois_Fighting_Illini_men's_basketball_team List(SportsSeason) Person -102.8982 1924%E2%80%9325_Illinois_Fighting_Illini_men's_basketball_team List(SportsSeason) Person -103.4483 1928%E2%80%9329_Wisconsin_Badgers_men's_basketball_team List(SportsSeason) Person -342.2507 1931%E2%80%9332_Michigan_Wolverines_men's_basketball_team List(SportsSeason) Person -586.6293 1935%E2%80%9336_Illinois_Fighting_Illini_men's_basketball_team List(SportsSeason) Person -102.789 1940%E2%80%9341_William_&_Mary_Indians_men's_basketball_team List(SportsSeason) Person -1077.7726 1943%E2%80%9344_William_&_Mary_Indians_men's_basketball_team List(SportsSeason) Person -861.7182 1948%E2%80%9349_Oklahoma_A&M_Aggies_men's_basketball_team List(SportsSeason) Person -201.7089 1953%E2%80%9354_Illinois_Fighting_Illini_men's_basketball_team List(SportsSeason) SportsSeason -109.6503 1953%E2%80%9354_St._Francis_Terriers_men's_basketball_team List(SportsSeason) Person -764.0718 1956%E2%80%9357_Georgetown_Hoyas_men's_basketball_team List(SportsSeason) Person -1136.1831 1958%E2%80%9359_Louisville_Cardinals_men's_basketball_team List(SportsSeason) Person -828.7416 1960%E2%80%9361_Michigan_Wolverines_men's_basketball_team List(SportsSeason) Person -366.3029 1965_NCAA_Division_I_Men's_Soccer_Championship List(Event) Person -508.3358 1969_European_Cup_Winners'_Cup_Final List(Event) Person -550.845 1970_NCAA_Division_I_Men's_Soccer_Championship List(Event) Person -504.0986 1973%E2%80%9374_Duke_Blue_Devils_men's_basketball_team List(SportsSeason) Person -344.3494 1975%E2%80%9376_Purdue_Boilermakers_men's_basketball_team List(SportsSeason) SportsSeason -135.3997 1980_European_Cup_Winners'_Cup_Final List(Event) Event -474.0882 1982%E2%80%9383_Princeton_Tigers_men's_basketball_team List(SportsSeason) Person -1964.5485 1983%E2%80%9384_Louisville_Cardinals_men's_basketball_team List(SportsSeason) Person -730.5695 1983%E2%80%9384_Oklahoma_Sooners_men's_basketball_team List(SportsSeason) Person -1674.8177 1984%E2%80%9385_Indiana_Hoosiers_men's_basketball_team List(SportsSeason) Person -271.0035 1984_NCAA_Division_I_Men's_Soccer_Championship List(Event) Person -592.132 1988%E2%80%9389_St._John's_Redmen_basketball_team List(SportsSeason) Person -440.392 1989%E2%80%9390_European_Cup_Winners'_Cup List(Event) Person -359.0593 1989_NCAA_Division_I_Men's_Soccer_Championship List(Event) Person -765.3048 1989_U.S._Women's_Open